In [1]:
import pandas as pd
import numpy as np
from pandas import Series, DataFrame
from decimal import Decimal
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 1000)

In [2]:
country_options = ['Germany','Great,Britain']
channel_options = ['Consumer,Electronic,Stores','Mass,Merchandisers/DIYSs']
year_options = [2016,2017,2018]
smart_connect_options = ['SMART,APP,CTRL.','VOICE,INTERAC.','VOICE,CONT.ONLY','n.a.','NO',Decimal('nan')]
smart_h_ecosys_options = ['n.a.','NOT,APPLICABLE','GOOG+AMZN','AMAZON,ALEXA','GOOGLE,HOME','APPLE,HOMEKIT',Decimal('nan')]
operating_ai_options = ['n.a.','NOT,APPLICABLE','GOOGLE,ASSISTAN','APPLE,SIRI','AMAZON,ALEXA',Decimal('nan')]
airplay_options = ['NO,AIRPLAY','AIRPLAY',Decimal('nan')]
googlecast_home_options = ['n.a.','NO,GOOGLECAST','GOOGLECAST/HOME',Decimal('nan')]
bluetooth_options = ['WITH,BLUETOOTH','W/O,BLUETOOTH','OPTIONAL',Decimal('nan')]
ethernet_options = ['NO,ETHERNET','ETHERNET',Decimal('nan')]
wifi_options = ['WIFI,BUILT-IN','NO,WIFI','WIFI,READY',Decimal('nan')]
high_res_audio_options = ['NO,HIGH-RES,AUD','HIGH-RES,AUDIO','n.a.',Decimal('nan')]
type_of_docking_options = ['BLUETOOTH,ONLY','NO,DOCKING/STRE','IOS/AIRPLAY','OTH.DOCK/STREAM','ANDR/GOOGLE,HOM','MULTIPLE']
multiroom_options = ['MULTIROOM','NO,MULTIROOM',Decimal('nan')]
no_speakerboxes_options = ['1','n.a.','0','2']
output_channel_options = [2,0]
streaming_connection_options = ['Bluetooth+Wifi','Bluetooth+Ethernet+Wifi','Wifi+Ethernet','Wifi','Ethernet','Bluetooth+Ethernet',Decimal('nan')]
streaming_technology_options = ['BT+UPNP','Proprietary,+BT','Bluetooth','n.a.','UPNP','BT+Airplay+UPNP',
                                'Proprietary,+BT,+Airplay,+UPNP','Airplay+UPNP','BT+Airplay,+UPNP,+Google,Cast/Home',
                                'Proprietary','Airplay','BT+UPNP,+Google,Cast/Home','BT+Google,Cast/Home','Bluetooth+Airplay',
                                'BT+Airplay,+Google,Cast/Home','Proprietary,+BT,+Airplay','Proprietary+Airplay',Decimal('nan')]
usb_connection_options = ['NO,USB','USB,TYPE-A/B',Decimal('nan')]
wattage_total_options = ['unknown','40','70','30','110','80','n.a.','150','90','60','45','300','5'
                         ,'240','140','154','50','20','29','75','14','55','92','38','15','320','25'
                         ,'10','72','13','100','130','200','120','18','65','250','180','175','36'
                         ,'17','450',Decimal('nan'),'35']

In [65]:
data = pd.DataFrame()

pivot_data_table = pd.DataFrame()
data_stats_table = pd.DataFrame()



unique_ids =[]

class sanitizeDataFrame():
    def __init__(self,data):
        self.data = data 
        self.monthsOrdered = ['16-Dec', '17-Jan', '17-Feb', '17-Mar', '17-Apr', '17-May', '17-Jun', '17-Jul', '17-Aug', '17-Sep', '17-Oct', '17-Nov', '17-Dec', '18-Jan', '18-Feb', '18-Mar', '18-Apr', '18-May','18-Jun', '18-Jul', '18-Aug', '18-Sep', '18-Oct', '18-Nov']
        self.columnsThatNeedATypeChange = ['sales_units', 'sales_value_eur', 'price_eur', 'sales_value_usd', 'price_usd']
        self.columnsToBeSortedBy = ['id','channel' ,'year','period']
        self.pivotcolumnsToBeSortedBy = ['id']
        self.setColumnNames = ['COUNTRY','CHANNEL' ,'BRAND','MODEL', 'ID','YEAR','PERIOD','SMART CONNECT','SMART H. ECOSYS', 'OPERATING AI','AIRPLAY','GOOGLECAST/HOME','BLUETOOTH','ETHERNET','WIFI','HEIGHT IN MM','WIDTH IN MM','HIGH-RES AUDIO', 'TYPE OF DOCKING','MULTIROOM','NO.SPEAKERBOXES','OUTPUT CHANNEL','Streaming Connection','Streaming Technology', 'USB CONNECTION','WATTAGE TOTAL','Sales Units','Sales Value EUR','Price EUR','Sales Value USD','Price USD']
        self.measurements_columns = ['height_in_mm','width_in_mm']
        self.key_stats_columns = [ 'id', 'country', 'channel', 'year', 'period', 'height_in_mm', 'width_in_mm','sales_units', 'sales_value_eur', 'price_eur', 'sales_value_usd', 'price_usd']
        self.pivot_key_columns = ['id','height_in_mm', 'width_in_mm','brand', 'model','smart_connect', 'smart_h._ecosys', 'operating_ai', 'airplay', 'googlecast/home', 'bluetooth', 'ethernet', 'wifi', 'high-res_audio', 'type_of_docking', 'multiroom', 'no.speakerboxes', 'output_channel', 'streaming_connection', 'streaming_technology', 'usb_connection', 'wattage_total']


        self.sanitize_df()
        
    def set_column_names(self):
        self.data.columns = self.setColumnNames

    def set_column_names_to_lower(self):
        self.data.columns = self.data.columns.str.replace(' ', '_').str.replace('.','').str.lower()

    def set_column_period_to_ordered_months(self):
        self.data.period.astype('category',categories=self.monthsOrdered)

    def set_to_numeric_for_these_columns(self,cols):
        for col in cols:
            self.data[col] = self.data[col].str.replace(',','').str.lower()
            self.data[col] = self.data[col].apply(pd.to_numeric, errors='coerce')

    def set_to_numeric_for_mesurement_columns(self,cols):
        for col in cols:
            self.data[col] = self.data[col].apply(pd.to_numeric, errors='coerce')

    def sort_values_based_on_these_columns(self,cols):
        self.data = self.data.sort_values(cols,inplace=False)

    def sanitize_df(self):
        self.set_column_names()
        self.set_column_names_to_lower()
        self.set_column_period_to_ordered_months()
        self.set_to_numeric_for_these_columns(self.columnsThatNeedATypeChange)
        self.set_to_numeric_for_mesurement_columns(self.measurements_columns)
        self.sort_values_based_on_these_columns(self.columnsToBeSortedBy)

    def get_df(self):
        return self.data
    
    def get_pivot_and_stats_data_tables(self):
        pivot_data_table = self.data.filter(items=self.pivot_key_columns)
        data_stats_table = self.data.filter(items=self.key_stats_columns)
        pivot_data_table = self.sort_df_values_based_on_these_columns(pivot_data_table,self.pivotcolumnsToBeSortedBy)
        data_stats_table = self.sort_df_values_based_on_these_columns(data_stats_table,self.columnsToBeSortedBy)
        return pivot_data_table,data_stats_table
    
    def sort_df_values_based_on_these_columns(self,df,cols):
        df = df.sort_values(cols,inplace=False)
        return df

    
class determineStats():
    def __init__(self):
        self.sales_columns =  ['sales_units','sales_value_eur', 'price_eur', 'sales_value_usd', 'price_usd']
        self.measurements_columns = ['height_in_mm','width_in_mm']
        self.pivot_key_columns = ['id','height_in_mm', 'width_in_mm','brand', 'model','smart_connect', 'smart_h._ecosys', 'operating_ai', 'airplay', 'googlecast/home', 'bluetooth', 'ethernet', 'wifi', 'high-res_audio', 'type_of_docking', 'multiroom', 'no.speakerboxes', 'output_channel', 'streaming_connection', 'streaming_technology', 'usb_connection', 'wattage_total']
        pass

    def get_describe_characterisitcs_for_sales_columns(self,firstRow,df,cols):
        for col in cols:
            self.sumCol = col + '_sum'
            self.sumCol = col + '_sum'
            self.meanCol = col + '_mean'
            self.medianCol = col + '_median'
            self.modeCol = col + '_mode'
            self.stdCol = col + '_std'
            self.minCol = col + '_min'
            self.maxCol = col + '_max'
            firstRow[self.sumCol]  = df[col].sum()
            firstRow[self.meanCol] = df[col].mean()
            firstRow[self.medianCol] = df[col].median()
            firstRow[self.modeCol] = df[col].mode()
            firstRow[self.stdCol] = df[col].std()
            firstRow[self.minCol] = df[col].min()
            firstRow[self.maxCol] = df[col].max()
#             firstRow = self.give_describe_characterisitcs(self,firstRow,df,col)
        return firstRow

    def get_describe_characterisitcs_for_measurement_columns(self,firstRow,df,cols):
        dfWithOutHeightAndWidth = df.dropna(subset=['height_in_mm','width_in_mm'],how='any')
        for col in cols:
            self.sumCol = col + '_sum'
            self.sumCol = col + '_sum'
            self.meanCol = col + '_mean'
            self.medianCol = col + '_median'
            self.modeCol = col + '_mode'
            self.stdCol = col + '_std'
            self.minCol = col + '_min'
            self.maxCol = col + '_max'
            firstRow[self.sumCol]  = df[col].sum()
            firstRow[self.meanCol] = df[col].mean()
            firstRow[self.medianCol] = df[col].median()
            firstRow[self.modeCol] = df[col].mode()
            firstRow[self.stdCol] = df[col].std()
            firstRow[self.minCol] = df[col].min()
            firstRow[self.maxCol] = df[col].max()
#             firstRow = self.give_describe_characterisitcs(firstRow,dfWithOutHeightAndWidth,col)
        return firstRow

    def get_sales_units(self,firstRow,df,cols):
        for col in cols:
            self.sumCol = col + '_sum'
            self.meanCol = col + '_mean'
            self.medianCol = col + '_median'
            self.modeCol = col + '_mode'
            self.stdCol = col + '_std'
            self.minCol = col + '_min'
            self.maxCol = col + '_max'
            firstRow[self.sumCol]  = df[col].sum()
            firstRow[self.meanCol] = df[col].mean()
            firstRow[self.medianCol] = df[col].median()
            firstRow[self.modeCol] = df[col].mode()
            firstRow[self.stdCol] = df[col].std()
            firstRow[self.minCol] = df[col].min()
            firstRow[self.maxCol] = df[col].max()
#             firstRow = self.give_describe_characterisitcs(firstRow,dfWithOutHeightAndWidth,col)
        return firstRow

    def get_sales_data_by_id(self, uni_ids, df):
        dfBasedOnID = pd.DataFrame()
        for uid in uni_ids:
            allDataBasedOnThisID = df[df['id']==uid]
            try:
                firstRow = allDataBasedOnThisID.iloc[0]
                try:
                    firstRow = self.get_describe_characterisitcs_for_sales_columns(firstRow,allDataBasedOnThisID,self.sales_columns)
                    try:
                        dfBasedOnID = dfBasedOnID.append(firstRow, ignore_index=True)
                    except:
                        print('cant append to dataframe')    
                except:
                    print('cant return first row for sales columns')
            except:
                print('no Id')
        print(dfBasedOnID)
        return dfBasedOnID
    
    def get_sales_total_sales_units(self,df):
        i = 1
        dfBasedOnID = pd.DataFrame()
        for uid in unique_ids:
            allDataBasedOnThisID = df[df['id']==uid]
            try:
                firstRow = allDataBasedOnThisID.iloc[0]
                try:
                    firstRow = self.get_describe_characterisitcs_for_sales_columns(firstRow,allDataBasedOnThisID,['sales_units'])
                    try:
                        dfBasedOnID = dfBasedOnID.append(firstRow, ignore_index=True)
                    except:
                        print('cant append to dataframe')    
                except:
                    print('cant return first row for sales columns')
            except:
                print('no Id')
            print(i)
            i += 1
        print(dfBasedOnID)
        return dfBasedOnID
    
    def get_measurements_data(self, uni_ids, df):
        i = 1
        dfBasedOnID = pd.DataFrame()
        for uid in uni_ids:
            allDataBasedOnThisID = df[df['id']==uid]
            try:
                firstRow = allDataBasedOnThisID.iloc[0]
                try:
                    firstRow = self.get_describe_characterisitcs_for_measurement_columns(firstRow,allDataBasedOnThisID,self.measurements_columns)
                    try:
                        dfBasedOnID = dfBasedOnID.append(firstRow, ignore_index=True)
                    except:
                        print('cant append to dataframe')    
                except:
                    print('cant return first row for sales columns')
            except:
                print('no Id')
            print(i)
            i += 1

        return dfBasedOnID
    
    def sort_by_id_only(self,df):
        i = 1
        dfBasedOnID = pd.DataFrame(columns=self.pivot_key_columns)
        print(unique_ids)
        for uid in unique_ids:
            allDataBasedOnThisID = df[df['id']==uid]
            try:
                firstRow = allDataBasedOnThisID.iloc[0]
                try:
                    dfBasedOnID = dfBasedOnID.append(firstRow, ignore_index=True)
                except:
                    print('cant append to dataframe')    
            except:
                print('no Id')

        return dfBasedOnID
    
    def get_dimensions(self,df):
        i = 1
        newDf = pd.DataFrame(columns=self.pivot_key_columns)
        try:
            firstRow = df.iloc[0]
            try:
                for col in self.measurements_columns:
                    self.sumCol = col + '_sum'
                    self.sumCol = col + '_sum'
                    self.meanCol = col + '_mean'
                    self.medianCol = col + '_median'
                    self.modeCol = col + '_mode'
                    self.stdCol = col + '_std'
                    self.minCol = col + '_min'
                    self.maxCol = col + '_max'
                    firstRow[self.sumCol]  = df[col].sum()
                    firstRow[self.meanCol] = df[col].mean()
                    firstRow[self.medianCol] = df[col].median()
                    firstRow[self.modeCol] = df[col].mode()
                    firstRow[self.stdCol] = df[col].std()
                    firstRow[self.minCol] = df[col].min()
                    firstRow[self.maxCol] = df[col].max()
                try:
                    return firstRow
                except:
                    print('cant append to dataframe')    
            except:
                print('cant for loop')  
        except:
            print('cant get df location 0')  

        return dfBasedOnID
    
    
def find_unique_of_this_column(data,col):
    return data[col].unique()
        

    

def read_csv(address):
    data = pd.read_csv(address,low_memory=False)
    return data


def main():
    '''
    send list of files to be parsed
    '''
    global unique_ids
    global data
    global pivot_data_table, data_stats_table
    address = './CSV_FILES/GfK_POS_Tracking-Smart_Audio_Home_Systems_DE_&_UK_python.csv'
    data = read_csv(address)
    santizeData = sanitizeDataFrame(data)
    data = santizeData.get_df()
    pivot_data_table,data_stats_table = santizeData.get_pivot_and_stats_data_tables()
    unique_ids = find_unique_of_this_column(data,'id')
    
    
#     create_specific_dfs(data)
    
    
    

if __name__ == "__main__": main()



/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:32: FutureWarning: specifying 'categories' or 'ordered' in .astype() is deprecated; pass a CategoricalDtype instead


In [4]:
# data

In [66]:
statsObj = determineStats()

In [6]:
total_sales_units_by_id = statsObj.get_sales_total_sales_units(data)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/pandas/core/series.py:915: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.loc[key] = value
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A va

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [7]:
total_sales_units_by_id 

airplay       bluetooth                     brand  \
0    NO AIRPLAY  WITH BLUETOOTH                     NOXON   
1    NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
2    NO AIRPLAY  WITH BLUETOOTH                        LG   
3    NO AIRPLAY  WITH BLUETOOTH                        LG   
4    NO AIRPLAY  WITH BLUETOOTH                        LG   
5    NO AIRPLAY   W/O BLUETOOTH                     SONOS   
6    NO AIRPLAY        OPTIONAL                     DENON   
7    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
8    NO AIRPLAY   W/O BLUETOOTH                POLK AUDIO   
9    NO AIRPLAY  WITH BLUETOOTH                POLK AUDIO   
10      AIRPLAY  WITH BLUETOOTH            BANG & OLUFSEN   
11   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
12   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
13   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
14   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
15   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
16   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
17   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
18   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
19   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
20   NO AIRPLAY   W/O BLUETOOTH                POLK AUDIO   
21      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
22   NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
23      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
24   NO AIRPLAY  WITH BLUETOOTH                   PHILIPS   
25      AIRPLAY   W/O BLUETOOTH                   AURALIC   
26      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
27      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
28      AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
29      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
30   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
31      AIRPLAY  WITH BLUETOOTH                      SONY   
32      AIRPLAY  WITH BLUETOOTH                      SONY   
33   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
34   NO AIRPLAY  WITH BLUETOOTH           MINISTRY OF SOU   
35   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
36      AIRPLAY  WITH BLUETOOTH            COCKTAIL AUDIO   
37   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
38   NO AIRPLAY   W/O BLUETOOTH                    MEDION   
39   NO AIRPLAY  WITH BLUETOOTH                      DYON   
40   NO AIRPLAY   W/O BLUETOOTH                POLK AUDIO   
41   NO AIRPLAY   W/O BLUETOOTH                POLK AUDIO   
42   NO AIRPLAY  WITH BLUETOOTH                     NUMAN   
43   NO AIRPLAY   W/O BLUETOOTH                 TECHNISAT   
44   NO AIRPLAY  WITH BLUETOOTH                     DENON   
45   NO AIRPLAY  WITH BLUETOOTH                     DENON   
46      AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
47   NO AIRPLAY   W/O BLUETOOTH                  PRO-JECT   
48   NO AIRPLAY   W/O BLUETOOTH                  ALBRECHT   
49      AIRPLAY   W/O BLUETOOTH           ELECTROCOMPANIE   
50   NO AIRPLAY   W/O BLUETOOTH           ELECTROCOMPANIE   
51   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
52   NO AIRPLAY  WITH BLUETOOTH                     BLOCK   
53   NO AIRPLAY   W/O BLUETOOTH                      ASUS   
54   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
55   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
56   NO AIRPLAY  WITH BLUETOOTH                     DENON   
57   NO AIRPLAY  WITH BLUETOOTH                      SONY   
58   NO AIRPLAY  WITH BLUETOOTH                     DENON   
59   NO AIRPLAY  WITH BLUETOOTH                     DENON   
60   NO AIRPLAY  WITH BLUETOOTH                     DENON   
61   NO AIRPLAY   W/O BLUETOOTH                  ALBRECHT   
62   NO AIRPLAY  WITH BLUETOOTH                      ILUV   
63   NO AIRPLAY  WITH BLUETOOTH                      SONY   
64   NO AIRPLAY  WITH BLUETOOTH            

In [8]:
total_sales_units_by_id.sort_values(['sales_units_sum'],ascending=False,inplace=True)

In [9]:
total_sales_units_by_id.to_csv('./CSV_FILES/By_Total_Units_Sold/total_units_sold_by_id.csv',index = None, header = True)

In [35]:
# total_sales_units_by_id

In [36]:
germany = data[data['country']=='Germany']

In [37]:
germany_total_sales_units_by_id = statsObj.get_sales_total_sales_units(germany)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:89: SettingWithCopyWarning: 
A value is trying to be set o

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
no Id
136
137
no Id
138
139
140
141
142
143
144
145
146
147
148
149
150
151
no Id
152
153
no Id
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
no Id
180
no Id
181
182
183
184
185
186
187
188
189
190
no Id
191
no Id
192
no Id
193
no Id
194
195
196
197
198
199
no Id
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
26

In [13]:
germany_total_sales_units_by_id.sort_values(['sales_units_sum'],ascending=False,inplace=True)

In [14]:
germany_total_sales_units_by_id

airplay       bluetooth                     brand  \
208  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
14   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
135  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
133  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
15   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
191  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
33   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
106  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
13   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
22   NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
186  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
127     AIRPLAY   W/O BLUETOOTH                     APPLE   
69      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
21      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
238  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
184  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
24   NO AIRPLAY  WITH BLUETOOTH                   PHILIPS   
58   NO AIRPLAY  WITH BLUETOOTH                     DENON   
92   NO AIRPLAY   W/O BLUETOOTH                      BOSE   
80   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
63   NO AIRPLAY  WITH BLUETOOTH                      SONY   
93   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
98   NO AIRPLAY  WITH BLUETOOTH                    SONORO   
136  NO AIRPLAY  WITH BLUETOOTH                      SONY   
67      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
119     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
162     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
173  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
55   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
11   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
6    NO AIRPLAY        OPTIONAL                     DENON   
1    NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
59   NO AIRPLAY  WITH BLUETOOTH                     DENON   
17   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
131  NO AIRPLAY  WITH BLUETOOTH                    SONORO   
51   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
19   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
224  NO AIRPLAY   W/O BLUETOOTH                     DENON   
222  NO AIRPLAY   W/O BLUETOOTH                     DENON   
7    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
110  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
35   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
57   NO AIRPLAY  WITH BLUETOOTH                      SONY   
78      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
192  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
5    NO AIRPLAY   W/O BLUETOOTH                     SONOS   
255  NO AIRPLAY   W/O BLUETOOTH  <Tradebrand & Exclusive>   
18   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
101     AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
123     AIRPLAY  WITH BLUETOOTH                RIVA AUDIO   
254  NO AIRPLAY   W/O BLUETOOTH  <Tradebrand & Exclusive>   
77      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
242  NO AIRPLAY  WITH BLUETOOTH             HARMAN-KARDON   
28      AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
0    NO AIRPLAY  WITH BLUETOOTH                     NOXON   
52   NO AIRPLAY  WITH BLUETOOTH                     BLOCK   
200  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
39   NO AIRPLAY  WITH BLUETOOTH                      DYON   
103  NO AIRPLAY  WITH BLUETOOTH                 TECHNISAT   
223  NO AIRPLAY   W/O BLUETOOTH                     DENON   
60   NO AIRPLAY  WITH BLUETOOTH                     DENON   
169     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
146     AIRPLAY  WITH BLUETOOTH                  MARSHALL   
154  NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
54   NO AIRPLAY  WITH BLUETOOTH            

In [15]:
germany_total_sales_units_by_id.to_csv('./CSV_FILES/By_Total_Units_Sold/germany_total_units_sold_by_id.csv',index = None, header = True)

In [16]:
britian = data[data['country']=='Great Britain']

In [17]:
great_britian_total_sales_units_by_id = statsObj.get_sales_total_sales_units(britian)

no Id
1
2
no Id
3
no Id
4
no Id
5


/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:89: SettingWithCopyWarning: 
A value is trying to be set o

6
7
8
no Id
9
no Id
10
no Id
11
no Id
12
no Id
13
14
15
16
no Id
17
18
19
20
no Id
21
22
23
no Id
24
25
26
27
28
29
30
no Id
31
32
33
34
no Id
35
no Id
36
no Id
37
no Id
38
no Id
39
no Id
40
no Id
41
no Id
42
no Id
43
no Id
44
45
no Id
46
47
no Id
48
no Id
49
no Id
50
no Id
51
52
no Id
53
no Id
54
55
56
57
58
59
60
61
no Id
62
no Id
63
64
no Id
65
66
no Id
67
68
no Id
69
70
71
no Id
72
no Id
73
no Id
74
no Id
75
no Id
76
no Id
77
78
79
no Id
80
81
no Id
82
no Id
83
no Id
84
no Id
85
no Id
86
87
88
no Id
89
90
no Id
91
no Id
92
93
94
no Id
95
no Id
96
no Id
97
no Id
98
no Id
99
no Id
100
no Id
101
102
no Id
103
no Id
104
no Id
105
no Id
106
107
no Id
108
no Id
109
no Id
110
111
no Id
112
113
114
no Id
115
no Id
116
no Id
117
no Id
118
no Id
119
120
no Id
121
122
no Id
123
124
125
126
no Id
127
128
no Id
129
no Id
130
131
no Id
132
no Id
133
134
135
136
137
138
139
no Id
140
no Id
141
no Id
142
no Id
143
no Id
144
no Id
145
146
147
no Id
148
149
150
151
152
no Id
153
154
no Id
155
no Id


In [18]:
great_britian_total_sales_units_by_id.sort_values(['sales_units_sum'],ascending=False,inplace=True)

In [19]:
great_britian_total_sales_units_by_id

airplay       bluetooth                     brand  \
56   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
67   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
58   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
92   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
76   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
45   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
59   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
5    NO AIRPLAY  WITH BLUETOOTH                      BOSE   
86   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
60   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
68   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
20   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
77   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
6    NO AIRPLAY  WITH BLUETOOTH                      BOSE   
54      AIRPLAY   W/O BLUETOOTH                     APPLE   
81   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
7    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
82   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
11   NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
75   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
83   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
4    NO AIRPLAY  WITH BLUETOOTH                      BOSE   
115  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
38   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
9    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
40   NO AIRPLAY   W/O BLUETOOTH                       JAM   
61   NO AIRPLAY  WITH BLUETOOTH                      SONY   
3    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
22      AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
78   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
110     AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
70   NO AIRPLAY  WITH BLUETOOTH                        LG   
31   NO AIRPLAY  WITH BLUETOOTH                      SONY   
0    NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
34      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
25   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
10      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
28   NO AIRPLAY  WITH BLUETOOTH                     DENON   
43   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
23   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
87   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
27   NO AIRPLAY  WITH BLUETOOTH                      SONY   
36      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
8    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
46   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
30   NO AIRPLAY  WITH BLUETOOTH                     DENON   
49      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
44      AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
2    NO AIRPLAY        OPTIONAL                     DENON   
137         NaN             NaN  <Tradebrand & Exclusive>   
37      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
132         NaN             NaN  <Tradebrand & Exclusive>   
18      AIRPLAY  WITH BLUETOOTH                      SONY   
52      AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
12   NO AIRPLAY  WITH BLUETOOTH                   PHILIPS   
138         NaN             NaN  <Tradebrand & Exclusive>   
65   NO AIRPLAY  WITH BLUETOOTH                     ONKYO   
103  NO AIRPLAY   W/O BLUETOOTH                     DENON   
74   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
69   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
29   NO AIRPLAY  WITH BLUETOOTH                     DENON   
35   NO AIRPLAY  WITH BLUETOOTH                   ROBERTS   
26   NO AIRPLAY  WITH BLUETOOTH                     DENON   
100  NO AIRPLAY  WITH BLUETOOTH                        LG   
101  NO AIRPLAY   W/O BLUETOOTH            

In [20]:
great_britian_total_sales_units_by_id.to_csv('./CSV_FILES/By_Total_Units_Sold/great_britian_total_sales_units_by_id.csv',index = None, header = True)

In [21]:
total_sales_units_by_id

airplay       bluetooth                     brand  \
219  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
133  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
151  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
135  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
136  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
14   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
180  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
106  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
202  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
15   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
33   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
137  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
127     AIRPLAY   W/O BLUETOOTH                     APPLE   
153  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
22   NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
13   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
189  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
196  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
194  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
249  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
193  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
17   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
69      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
21      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
179  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
80   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
24   NO AIRPLAY  WITH BLUETOOTH                   PHILIPS   
58   NO AIRPLAY  WITH BLUETOOTH                     DENON   
138  NO AIRPLAY  WITH BLUETOOTH                      SONY   
19   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
63   NO AIRPLAY  WITH BLUETOOTH                      SONY   
7    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
93   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
87   NO AIRPLAY   W/O BLUETOOTH                       JAM   
92   NO AIRPLAY   W/O BLUETOOTH                      BOSE   
55   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
1    NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
46      AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
190  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
243     AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
98   NO AIRPLAY  WITH BLUETOOTH                    SONORO   
164  NO AIRPLAY  WITH BLUETOOTH                        LG   
119     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
51   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
67      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
177  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
166     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
203  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
6    NO AIRPLAY        OPTIONAL                     DENON   
57   NO AIRPLAY  WITH BLUETOOTH                      SONY   
110  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
59   NO AIRPLAY  WITH BLUETOOTH                     DENON   
18   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
77      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
11   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
235  NO AIRPLAY   W/O BLUETOOTH                     DENON   
78      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
233  NO AIRPLAY   W/O BLUETOOTH                     DENON   
101     AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
131  NO AIRPLAY  WITH BLUETOOTH                    SONORO   
60   NO AIRPLAY  WITH BLUETOOTH                     DENON   
35   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
5    NO AIRPLAY   W/O BLUETOOTH                     SONOS   
28      AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
286  NO AIRPLAY   W/O BLUETOOTH  <Tradebran

In [22]:
germany_total_sales_units_by_id

airplay       bluetooth                     brand  \
208  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
14   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
135  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
133  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
15   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
191  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
33   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
106  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
13   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
22   NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
186  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
127     AIRPLAY   W/O BLUETOOTH                     APPLE   
69      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
21      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
238  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
184  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
24   NO AIRPLAY  WITH BLUETOOTH                   PHILIPS   
58   NO AIRPLAY  WITH BLUETOOTH                     DENON   
92   NO AIRPLAY   W/O BLUETOOTH                      BOSE   
80   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
63   NO AIRPLAY  WITH BLUETOOTH                      SONY   
93   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
98   NO AIRPLAY  WITH BLUETOOTH                    SONORO   
136  NO AIRPLAY  WITH BLUETOOTH                      SONY   
67      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
119     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
162     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
173  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
55   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
11   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
6    NO AIRPLAY        OPTIONAL                     DENON   
1    NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
59   NO AIRPLAY  WITH BLUETOOTH                     DENON   
17   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
131  NO AIRPLAY  WITH BLUETOOTH                    SONORO   
51   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
19   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
224  NO AIRPLAY   W/O BLUETOOTH                     DENON   
222  NO AIRPLAY   W/O BLUETOOTH                     DENON   
7    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
110  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
35   NO AIRPLAY  WITH BLUETOOTH                 BLUESOUND   
57   NO AIRPLAY  WITH BLUETOOTH                      SONY   
78      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
192  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
5    NO AIRPLAY   W/O BLUETOOTH                     SONOS   
255  NO AIRPLAY   W/O BLUETOOTH  <Tradebrand & Exclusive>   
18   NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
101     AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
123     AIRPLAY  WITH BLUETOOTH                RIVA AUDIO   
254  NO AIRPLAY   W/O BLUETOOTH  <Tradebrand & Exclusive>   
77      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
242  NO AIRPLAY  WITH BLUETOOTH             HARMAN-KARDON   
28      AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
0    NO AIRPLAY  WITH BLUETOOTH                     NOXON   
52   NO AIRPLAY  WITH BLUETOOTH                     BLOCK   
200  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
39   NO AIRPLAY  WITH BLUETOOTH                      DYON   
103  NO AIRPLAY  WITH BLUETOOTH                 TECHNISAT   
223  NO AIRPLAY   W/O BLUETOOTH                     DENON   
60   NO AIRPLAY  WITH BLUETOOTH                     DENON   
169     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
146     AIRPLAY  WITH BLUETOOTH                  MARSHALL   
154  NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
54   NO AIRPLAY  WITH BLUETOOTH            

In [23]:
great_britian_total_sales_units_by_id

airplay       bluetooth                     brand  \
56   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
67   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
58   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
92   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
76   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
45   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
59   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
5    NO AIRPLAY  WITH BLUETOOTH                      BOSE   
86   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
60   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
68   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
20   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
77   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
6    NO AIRPLAY  WITH BLUETOOTH                      BOSE   
54      AIRPLAY   W/O BLUETOOTH                     APPLE   
81   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
7    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
82   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
11   NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
75   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
83   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
4    NO AIRPLAY  WITH BLUETOOTH                      BOSE   
115  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
38   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
9    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
40   NO AIRPLAY   W/O BLUETOOTH                       JAM   
61   NO AIRPLAY  WITH BLUETOOTH                      SONY   
3    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
22      AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
78   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
110     AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
70   NO AIRPLAY  WITH BLUETOOTH                        LG   
31   NO AIRPLAY  WITH BLUETOOTH                      SONY   
0    NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
34      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
25   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
10      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
28   NO AIRPLAY  WITH BLUETOOTH                     DENON   
43   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
23   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
87   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
27   NO AIRPLAY  WITH BLUETOOTH                      SONY   
36      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
8    NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
46   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
30   NO AIRPLAY  WITH BLUETOOTH                     DENON   
49      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
44      AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
2    NO AIRPLAY        OPTIONAL                     DENON   
137         NaN             NaN  <Tradebrand & Exclusive>   
37      AIRPLAY  WITH BLUETOOTH                    YAMAHA   
132         NaN             NaN  <Tradebrand & Exclusive>   
18      AIRPLAY  WITH BLUETOOTH                      SONY   
52      AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
12   NO AIRPLAY  WITH BLUETOOTH                   PHILIPS   
138         NaN             NaN  <Tradebrand & Exclusive>   
65   NO AIRPLAY  WITH BLUETOOTH                     ONKYO   
103  NO AIRPLAY   W/O BLUETOOTH                     DENON   
74   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
69   NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
29   NO AIRPLAY  WITH BLUETOOTH                     DENON   
35   NO AIRPLAY  WITH BLUETOOTH                   ROBERTS   
26   NO AIRPLAY  WITH BLUETOOTH                     DENON   
100  NO AIRPLAY  WITH BLUETOOTH                        LG   
101  NO AIRPLAY   W/O BLUETOOTH            

In [39]:
def top_50(df):
    newDf = pd.DataFrame()
    count = 0
    while count < 50:
        count=count+1;
        firstRow = df.iloc[count]
        try:
            newDf = newDf.append(firstRow, ignore_index=True)
        except:
            print('cant append to dataframe') 
    return newDf


In [40]:
top_50_by_id = top_50(total_sales_units_by_id)

In [41]:
top_50_by_id.to_csv('./CSV_FILES/Top_50/top_50_by_id.csv',index = None, header = True)

In [42]:
top_50_by_germany = top_50(germany_total_sales_units_by_id)

In [43]:
top_50_by_germany.to_csv('./CSV_FILES/Top_50/top_50_by_germany.csv',index = None, header = True)

In [44]:
top_50_by_britain = top_50(great_britian_total_sales_units_by_id)

In [45]:
top_50_by_britain.to_csv('./CSV_FILES/Top_50/top_50_by_britain.csv',index = None, header = True)

In [46]:
top_50_by_id_unique_ids = top_50_by_id.id.unique()

In [47]:
top_50_by_germany_unique_ids = top_50_by_germany.id.unique()

In [48]:
top_50_by_britain_unique_ids = top_50_by_britain.id.unique()

In [49]:
top_50_by_britain_unique_ids

array(['139642623', '134170754', '85567274', '149663289', '121592309',
       '134232746', '105262570', '64803096', '134233609', '140024566',
       '106563503', '150503060', '105262595', '129509034', '150517535',
       '105568370', '42981578', '105873415', '149634117', '43055286',
       '105227304', '95309560', '116785298', '105735857', '118021988',
       '136387538', '102402338', '109589437', '150503454', '95002534',
       '143351029', '114883726', '100671708', '115572054', '111607890',
       '105817564', '112624845', '118504472', '110750097', '64844543',
       '112576020', '116776378', '105735826', '122545224', '112737335',
       '123886929', '119276744', '102345694', 'C3893362561', '116776911'],
      dtype=object)

In [50]:
top_50_sales_data_by_id = statsObj.get_sales_data_by_id(top_50_by_id_unique_ids,data)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:89: SettingWithCopyWarning: 
A value is trying to be set o

       airplay       bluetooth       brand                     channel  \
0   NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
1   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
2   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
3   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
4   NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
5   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
6   NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
7   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
8   NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
9   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
10  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
11     AIRPLAY   W/O BLUETOOTH       APPLE  Consumer Electronic Stores   
12  NO AIRPLAY  WITH BLUETOOTH      AM

In [51]:
top_50_sales_data_by_id

airplay       bluetooth       brand                     channel  \
0   NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
1   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
2   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
3   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
4   NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
5   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
6   NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
7   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
8   NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
9   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
10  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
11     AIRPLAY   W/O BLUETOOTH       APPLE  Consumer Electronic Stores   
12  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
13  NO AIRPLAY   W/O BLUETOOTH      GOOGLE  Consumer Electronic Stores   
14  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
15  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
16  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
17  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
18  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
19  NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
20  NO AIRPLAY  WITH BLUETOOTH     SAMSUNG  Consumer Electronic Stores   
21     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
22     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
23  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
24  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
25  NO AIRPLAY  WITH BLUETOOTH     PHILIPS  Consumer Electronic Stores   
26  NO AIRPLAY  WITH BLUETOOTH       DENON  Consumer Electronic Stores   
27  NO AIRPLAY  WITH BLUETOOTH        SONY  Consumer Electronic Stores   
28  NO AIRPLAY  WITH BLUETOOTH     SAMSUNG  Consumer Electronic Stores   
29  NO AIRPLAY  WITH BLUETOOTH        SONY  Consumer Electronic Stores   
30  NO AIRPLAY  WITH BLUETOOTH     SAMSUNG  Consumer Electronic Stores   
31  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
32  NO AIRPLAY   W/O BLUETOOTH         JAM  Consumer Electronic Stores   
33  NO AIRPLAY   W/O BLUETOOTH        BOSE  Consumer Electronic Stores   
34  NO AIRPLAY  WITH BLUETOOTH   PANASONIC  Consumer Electronic Stores   
35  NO AIRPLAY  WITH BLUETOOTH   PANASONIC  Consumer Electronic Stores   
36     AIRPLAY  WITH BLUETOOTH  NAIM AUDIO  Consumer Electronic Stores   
37  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
38     AIRPLAY  WITH BLUETOOTH  NAIM AUDIO  Consumer Electronic Stores   
39  NO AIRPLAY  WITH BLUETOOTH      SONORO  Consumer Electronic Stores   
40  NO AIRPLAY  WITH BLUETOOTH          LG  Consumer Electronic Stores   
41     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
42  NO AIRPLAY  WITH BLUETOOTH   PANASONIC  Consumer Electronic Stores   
43     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
44  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
45     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
46  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
47  NO AIRPLAY        OPTIONAL       DENON  Consumer Electronic Stores   
48  NO AIRPLAY  WITH BLUETOOTH        SONY  Consumer Electronic Stores   
49  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   

          country     ethernet  googlecast/home  height_in_mm  \
0         Germany  NO ETHERNET  GOOGLECAST/HOME         42.00   
1   Great Britain     ETHERNET    NO GOOGLECAST         32.00   
2   Great Britain  NO ETHERNET    NO 

In [52]:
top_50_sales_data_by_germany = statsObj.get_sales_data_by_id(top_50_by_germany_unique_ids,data)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:89: SettingWithCopyWarning: 
A value is trying to be set o

       airplay       bluetooth            brand                     channel  \
0   NO AIRPLAY  WITH BLUETOOTH        PANASONIC  Consumer Electronic Stores   
1   NO AIRPLAY  WITH BLUETOOTH               LG  Consumer Electronic Stores   
2   NO AIRPLAY  WITH BLUETOOTH               LG  Consumer Electronic Stores   
3   NO AIRPLAY  WITH BLUETOOTH               LG  Consumer Electronic Stores   
4   NO AIRPLAY   W/O BLUETOOTH            SONOS  Consumer Electronic Stores   
5   NO AIRPLAY        OPTIONAL            DENON  Consumer Electronic Stores   
6   NO AIRPLAY  WITH BLUETOOTH          SAMSUNG  Consumer Electronic Stores   
7   NO AIRPLAY   W/O BLUETOOTH       POLK AUDIO  Consumer Electronic Stores   
8   NO AIRPLAY  WITH BLUETOOTH       POLK AUDIO  Consumer Electronic Stores   
9      AIRPLAY  WITH BLUETOOTH   BANG & OLUFSEN  Consumer Electronic Stores   
10  NO AIRPLAY  WITH BLUETOOTH        BLUESOUND  Consumer Electronic Stores   
11  NO AIRPLAY  WITH BLUETOOTH        BLUESOUND  Con

In [53]:
top_50_sales_data_by_britian = statsObj.get_sales_data_by_id(top_50_by_britain_unique_ids,data)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:89: SettingWithCopyWarning: 
A value is trying to be set o

       airplay       bluetooth                     brand  \
0   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
1   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
2   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
3   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
4   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
5   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
6   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
7   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
8   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
9   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
10  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
11  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
12  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
13     AIRPLAY   W/O BLUETOOTH                     APPLE   
14  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
15  NO AIRPLAY  WITH BLUETOOTH          

In [54]:
top_50_sales_data_by_id.to_csv('./CSV_FILES/Top_50_Sales_Data/top_50_sales_data_by_id.csv',index = None, header = True)

In [55]:
top_50_sales_data_by_germany.to_csv('./CSV_FILES/Top_50_Sales_Data/top_50_sales_data_by_germany.csv',index = None, header = True)

In [56]:
top_50_sales_data_by_britian.to_csv('./CSV_FILES/Top_50_Sales_Data/top_50_sales_data_by_britian.csv',index = None, header = True)

In [57]:
top_50_sales_data_by_id

airplay       bluetooth       brand                     channel  \
0   NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
1   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
2   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
3   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
4   NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
5   NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
6   NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
7   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
8   NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
9   NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
10  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
11     AIRPLAY   W/O BLUETOOTH       APPLE  Consumer Electronic Stores   
12  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
13  NO AIRPLAY   W/O BLUETOOTH      GOOGLE  Consumer Electronic Stores   
14  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
15  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
16  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
17  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
18  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
19  NO AIRPLAY  WITH BLUETOOTH      GOOGLE  Consumer Electronic Stores   
20  NO AIRPLAY  WITH BLUETOOTH     SAMSUNG  Consumer Electronic Stores   
21     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
22     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
23  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
24  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
25  NO AIRPLAY  WITH BLUETOOTH     PHILIPS  Consumer Electronic Stores   
26  NO AIRPLAY  WITH BLUETOOTH       DENON  Consumer Electronic Stores   
27  NO AIRPLAY  WITH BLUETOOTH        SONY  Consumer Electronic Stores   
28  NO AIRPLAY  WITH BLUETOOTH     SAMSUNG  Consumer Electronic Stores   
29  NO AIRPLAY  WITH BLUETOOTH        SONY  Consumer Electronic Stores   
30  NO AIRPLAY  WITH BLUETOOTH     SAMSUNG  Consumer Electronic Stores   
31  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
32  NO AIRPLAY   W/O BLUETOOTH         JAM  Consumer Electronic Stores   
33  NO AIRPLAY   W/O BLUETOOTH        BOSE  Consumer Electronic Stores   
34  NO AIRPLAY  WITH BLUETOOTH   PANASONIC  Consumer Electronic Stores   
35  NO AIRPLAY  WITH BLUETOOTH   PANASONIC  Consumer Electronic Stores   
36     AIRPLAY  WITH BLUETOOTH  NAIM AUDIO  Consumer Electronic Stores   
37  NO AIRPLAY  WITH BLUETOOTH      AMAZON  Consumer Electronic Stores   
38     AIRPLAY  WITH BLUETOOTH  NAIM AUDIO  Consumer Electronic Stores   
39  NO AIRPLAY  WITH BLUETOOTH      SONORO  Consumer Electronic Stores   
40  NO AIRPLAY  WITH BLUETOOTH          LG  Consumer Electronic Stores   
41     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
42  NO AIRPLAY  WITH BLUETOOTH   PANASONIC  Consumer Electronic Stores   
43     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
44  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   
45     AIRPLAY  WITH BLUETOOTH      YAMAHA  Consumer Electronic Stores   
46  NO AIRPLAY   W/O BLUETOOTH       SONOS  Consumer Electronic Stores   
47  NO AIRPLAY        OPTIONAL       DENON  Consumer Electronic Stores   
48  NO AIRPLAY  WITH BLUETOOTH        SONY  Consumer Electronic Stores   
49  NO AIRPLAY  WITH BLUETOOTH        BOSE  Consumer Electronic Stores   

          country     ethernet  googlecast/home  height_in_mm  \
0         Germany  NO ETHERNET  GOOGLECAST/HOME         42.00   
1   Great Britain     ETHERNET    NO GOOGLECAST         32.00   
2   Great Britain  NO ETHERNET    NO 

In [67]:
top_50_measurements_data_by_id = statsObj.get_measurements_data(top_50_by_id_unique_ids,top_50_sales_data_by_id)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:108: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:109: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:110: SettingWithCopyWarning: 
A value is trying to be s

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50


In [68]:
top_50_measurements_data_by_germany = statsObj.get_measurements_data(top_50_by_germany_unique_ids,top_50_sales_data_by_germany)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:108: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:109: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:110: SettingWithCopyWarning: 
A value is trying to be s

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50


In [69]:
top_50_measurements_data_by_britian = statsObj.get_measurements_data(top_50_by_britain_unique_ids,top_50_sales_data_by_britian)

/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:108: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:109: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/mike/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:110: SettingWithCopyWarning: 
A value is trying to be s

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50


In [74]:
top_50_measurements_data_by_id.to_csv('./CSV_FILES/Top_50_Measure_Ments_Data/top_50_measurements_data_by_id.csv',index = None, header = True)

In [75]:
top_50_measurements_data_by_germany.to_csv('./CSV_FILES/Top_50_Measure_Ments_Data/top_50_measurements_data_by_germany.csv',index = None, header = True)

In [76]:
top_50_measurements_data_by_britian.to_csv('./CSV_FILES/Top_50_Measure_Ments_Data/top_50_measurements_data_by_britian.csv',index = None, header = True)

In [77]:
top_50_measurements_data_by_britian

airplay       bluetooth                     brand  \
0   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
1   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
2   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
3   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
4   NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
5   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
6   NO AIRPLAY  WITH BLUETOOTH                      BOSE   
7   NO AIRPLAY   W/O BLUETOOTH                     SONOS   
8   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
9   NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
10  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
11  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
12  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
13     AIRPLAY   W/O BLUETOOTH                     APPLE   
14  NO AIRPLAY  WITH BLUETOOTH                    GOOGLE   
15  NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
16  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
17  NO AIRPLAY   W/O BLUETOOTH                    GOOGLE   
18  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
19  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
20  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
21  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
22  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
23  NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
24  NO AIRPLAY   W/O BLUETOOTH                       JAM   
25  NO AIRPLAY  WITH BLUETOOTH                      SONY   
26  NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
27     AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
28  NO AIRPLAY  WITH BLUETOOTH                    AMAZON   
29     AIRPLAY  WITH BLUETOOTH                NAIM AUDIO   
30  NO AIRPLAY  WITH BLUETOOTH                        LG   
31  NO AIRPLAY  WITH BLUETOOTH                      SONY   
32  NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
33     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
34  NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
35     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
36  NO AIRPLAY  WITH BLUETOOTH                     DENON   
37  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
38  NO AIRPLAY  WITH BLUETOOTH                 PANASONIC   
39  NO AIRPLAY   W/O BLUETOOTH                     SONOS   
40  NO AIRPLAY  WITH BLUETOOTH                      SONY   
41     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
42  NO AIRPLAY  WITH BLUETOOTH                   SAMSUNG   
43  NO AIRPLAY  WITH BLUETOOTH                      BOSE   
44  NO AIRPLAY  WITH BLUETOOTH                     DENON   
45     AIRPLAY  WITH BLUETOOTH                    YAMAHA   
46     AIRPLAY  WITH BLUETOOTH                  B&O PLAY   
47  NO AIRPLAY        OPTIONAL                     DENON   
48         NaN             NaN  <Tradebrand & Exclusive>   
49     AIRPLAY  WITH BLUETOOTH                    YAMAHA   

                       channel        country     ethernet  googlecast/home  \
0   Consumer Electronic Stores  Great Britain     ETHERNET    NO GOOGLECAST   
1   Consumer Electronic Stores  Great Britain  NO ETHERNET    NO GOOGLECAST   
2   Consumer Electronic Stores        Germany     ETHERNET    NO GOOGLECAST   
3   Consumer Electronic Stores  Great Britain  NO ETHERNET    NO GOOGLECAST   
4   Consumer Electronic Stores  Great Britain  NO ETHERNET  GOOGLECAST/HOME   
5   Consumer Electronic Stores        Germany     ETHERNET    NO GOOGLECAST   
6   Consumer Electronic Stores        Germany  NO ETHERNET    NO GOOGLECAST   
7   Consumer Electronic Stores        Germany     ETHERNET    NO GOOGLECAST   
8   Consumer Electronic Stores  Great Britain  NO ETHERNET    NO GOOGLECAST   
9   Consumer Electronic Stores  Great Britain  NO ETHERNET    NO GOOGLECAST   
10  Consumer Electronic Stores        Germany     ETHERNET    NO GOOGLECAST  

In [87]:
# avg_dimesions_britian = statsObj.get_dimensions(top_50_measurements_data_by_britian)

In [86]:
# avg_dimesions_germany = statsObj.get_dimensions(top_50_measurements_data_by_germany)

In [ ]:
# top_50_measurements_data_by_id

In [85]:
# avg_dimesions_data_by_id = statsObj.get_dimensions(top_50_measurements_data_by_id)

In [84]:
# avg_dimesions_data_by_id

In [88]:
avg_dimesions_britian.to_csv('./CSV_FILES/Top_50_Avg_Dimensions/avg_dimesions_britian.csv',index = None, header = True)

In [89]:
avg_dimesions_germany.to_csv('./CSV_FILES/Top_50_Avg_Dimensions/avg_dimesions_germany.csv',index = None, header = True)

In [90]:
avg_dimesions_data_by_id.to_csv('./CSV_FILES/Top_50_Avg_Dimensions/avg_dimesions_data_by_id.csv',index = None, header = True)

In [ ]:
# collectedID = sort_by_id(data_stats_table)

In [ ]:
# collectedID

In [ ]:
# collectedID.columns

In [ ]:
len(unique_ids)